# AKSST (Ported from Jordan... R)

## Using pandas and altair

In [360]:
import altair as alt
from altair.expr import datum
import pandas as pd
import datetime

In [361]:
source = 'https://apex.psmfc.org/akfin/data_marts/akmp/GET_TIME_SERIES_REGIONAL_AVG_TEMPS'

In [362]:
df = pd.read_csv(source)
df['DateTime']= df.apply(lambda row: pd.datetime.strptime(str(row['YEAR'])+' '+str(row['JULIAN']),'%Y %j'), axis=1)


/Users/bell/anaconda2/envs/py37/lib/python3.7/site-packages/ipykernel_launcher.py:2: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  


In [363]:
#summary of the dataset
df

MEANSST   ESR_REGION               READ_DATE  YEAR  JULIAN   DateTime
0         4.37          EBS  06/02/2002 09:00:00 AM  2002     153 2002-06-02
1         7.71         EGOA  06/02/2002 09:00:00 AM  2002     153 2002-06-02
2         1.61          NBS  06/02/2002 09:00:00 AM  2002     153 2002-06-02
3         4.83        Other  06/02/2002 09:00:00 AM  2002     153 2002-06-02
4         7.54  SEAK Inside  06/02/2002 09:00:00 AM  2002     153 2002-06-02
...        ...          ...                     ...   ...     ...        ...
39589    11.52         EGOA  06/29/2020 09:00:00 AM  2020     181 2020-06-29
39590     7.22          NBS  06/29/2020 09:00:00 AM  2020     181 2020-06-29
39591     7.42        Other  06/29/2020 09:00:00 AM  2020     181 2020-06-29
39592    11.40  SEAK Inside  06/29/2020 09:00:00 AM  2020     181 2020-06-29
39593    10.33         WGOA  06/29/2020 09:00:00 AM  2020     181 2020-06-29

[39594 rows x 6 columns]

In [364]:
datestamp = df.DateTime.max()

In [365]:
## some basic housekeeping... 
# a limitiation of altair / javascript
alt.data_transformers.disable_max_rows()

#  Load 508 compliant NOAA colors
OceansBlue1='#0093D0'
OceansBlue2='#0055A4' # rebecca dark blue
CoralRed1='#FF4438'
SeagrassGreen1='#93D500'
SeagrassGreen4='#D0D0D0' # This is just grey
UrchinPurple1='#7F7FFF'
WavesTeal1='#1ECAD3'

## Just one region (EBS) with climatology overplotted

In [366]:
#transformation
#group by regions

dfg=df.groupby('ESR_REGION')
dfg.groups.keys()

dict_keys(['EBS', 'EGOA', 'NBS', 'Other', 'SEAK Inside', 'WGOA'])

In [367]:
subset = dfg.get_group('EBS')
subset

MEANSST ESR_REGION               READ_DATE  YEAR  JULIAN   DateTime
0         4.37        EBS  06/02/2002 09:00:00 AM  2002     153 2002-06-02
6         4.47        EBS  06/03/2002 09:00:00 AM  2002     154 2002-06-03
12        4.81        EBS  06/04/2002 09:00:00 AM  2002     155 2002-06-04
18        5.12        EBS  06/05/2002 09:00:00 AM  2002     156 2002-06-05
24        5.26        EBS  06/06/2002 09:00:00 AM  2002     157 2002-06-06
...        ...        ...                     ...   ...     ...        ...
39564     8.62        EBS  06/25/2020 09:00:00 AM  2020     177 2020-06-25
39570     8.42        EBS  06/26/2020 09:00:00 AM  2020     178 2020-06-26
39576     8.51        EBS  06/27/2020 09:00:00 AM  2020     179 2020-06-27
39582     8.42        EBS  06/28/2020 09:00:00 AM  2020     180 2020-06-28
39588     8.86        EBS  06/29/2020 09:00:00 AM  2020     181 2020-06-29

[6599 rows x 6 columns]

In [373]:
selector = alt.selection_single(
    fields=['YEAR'], 
    empty='all',
    bind='legend'
)


pastyearscolor=['#D0D0D0']*17
pastyears= [(x) for x in range(2002,2019,1)]
scale = alt.Scale(domain=pastyears + [2019,2020],
                  range=pastyearscolor+['#1ECAD3', '#0055A4'])

current = alt.Chart(subset
).mark_line(
    color='grey',
    clip=True
).encode(
    alt.X('monthdate(DateTime):T',title='',axis=alt.Axis(format='%b')),
    alt.Y('MEANSST:Q',title='SST'),
    alt.Color('YEAR:N',scale=scale),
    opacity=alt.condition(selector, alt.value(1), alt.value(0))
).add_selection(
    selector
)

mean = alt.Chart(subset
).mark_line(
    color='black',
    clip=True
).encode(
    alt.X('monthdate(DateTime):T'),
    alt.Y('mean(MEANSST):Q'),
).transform_filter(
    alt.FieldLTEPredicate('YEAR', 2012)
)

(current+mean).configure_axis(
    grid=False
).configure_view(
    strokeWidth=0
).properties(
    width=375,
    height=300
).properties(
    background='#f4f4f4',
    title='MUR SST EBS'
).configure(
# fix that pesky title
    title=alt.TitleConfig(fontSize=14, anchor='middle', offset=10),
    legend=alt.LegendConfig(labelFontSize=12, titleFontSize=12, symbolSize=100, offset=10)
).interactive()

alt.LayerChart(...)

## All Regions with regional climatology

In [375]:
#base chart setup below
current = alt.Chart(df
).mark_line(
    color='grey',
    clip=True
).encode(
    alt.X('monthdate(DateTime):T',title='',axis=alt.Axis(format='%b')),
    alt.Y('MEANSST:Q',title='SST'),
    alt.Color('YEAR:N',scale=scale),
    opacity=alt.condition(selector, alt.value(1), alt.value(0))
).add_selection(
    selector
).properties(
    width=250,
    height=200
)

mean = alt.Chart(df
).mark_line(
    color='black',
    clip=True
).encode(
    alt.X('monthdate(DateTime):T'),
    alt.Y('mean(MEANSST):Q'),
).transform_filter(
    alt.FieldLTEPredicate('YEAR', 2012)
)

base_chart = (current+mean)

# chart factory
def make_chart(base_chart, region, options):
    title = f'{region}'
    chart = base_chart\
      .transform_filter(datum.ESR_REGION == region)\
      .properties(title=title)
    return chart

In [376]:
options = {'width': 150, 'height': 150}
charts = [make_chart(base_chart, region, options) for region in sorted(df['ESR_REGION'].unique())]
allcharts = alt.VConcatChart(vconcat=[alt.HConcatChart(hconcat=charts[0:3]),
                          alt.HConcatChart(hconcat=charts[3::])])

allcharts_final = allcharts.properties(
    background='#f4f4f4',
    title=f"MUR SST AK Regions valid through {datestamp.strftime('%b %d %Y')}"
).configure(
# fix that pesky title
    title=alt.TitleConfig(fontSize=14, anchor='middle', offset=10),
    legend=alt.LegendConfig(labelFontSize=12, titleFontSize=12, symbolSize=100, offset=10)
)

allcharts_final

alt.VConcatChart(...)

In [371]:
allcharts_final.save('AKSST_allcharts_final.html', embed_options={'renderer':'svg'})